In [2]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)


In [6]:
import pandas as pd
import warnings
warnings.filterwarnings("ignore")

In [4]:
df_raw = pd.read_csv('../Assets/bird_tracking.csv')
df_raw.head()

Unnamed: 0  altitude               date_time  device_info_serial  \
0           0        71  2013-08-15 00:18:08+00                 851   
1           1        68  2013-08-15 00:48:07+00                 851   
2           2        68  2013-08-15 01:17:58+00                 851   
3           3        73  2013-08-15 01:47:51+00                 851   
4           4        69  2013-08-15 02:17:42+00                 851   

    direction   latitude  longitude  speed_2d bird_name  
0 -150.469753  49.419860   2.120733  0.150000      Eric  
1 -136.151141  49.419880   2.120746  2.438360      Eric  
2  160.797477  49.420310   2.120885  0.596657      Eric  
3   32.769360  49.420359   2.120859  0.310161      Eric  
4   45.191230  49.420331   2.120887  0.193132      Eric

In [5]:
df_raw.shape

(61920, 9)

In [7]:
df_raw['bird_name'].unique()


array(['Eric', 'Nico', 'Sanne'], dtype=object)

In [8]:
start_date = df_raw['date_time'].min()
end_date = df_raw['date_time'].max()

print(f"Start date: {start_date}")
print(f"End date: {end_date}")


Start date: 2013-08-15 00:01:08+00
End date: 2014-04-30 23:59:34+00


In [9]:
df_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 61920 entries, 0 to 61919
Data columns (total 9 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Unnamed: 0          61920 non-null  int64  
 1   altitude            61920 non-null  int64  
 2   date_time           61920 non-null  object 
 3   device_info_serial  61920 non-null  int64  
 4   direction           61477 non-null  float64
 5   latitude            61920 non-null  float64
 6   longitude           61920 non-null  float64
 7   speed_2d            61477 non-null  float64
 8   bird_name           61920 non-null  object 
dtypes: float64(4), int64(3), object(2)
memory usage: 4.3+ MB


In [10]:
df_raw.describe()

Unnamed: 0      altitude  device_info_serial     direction  \
count  61920.000000  61920.000000        61920.000000  61477.000000   
mean   30959.500000     52.313275          849.328505     -4.610841   
std    17874.908671    136.435498           12.835870    102.786009   
min        0.000000  -1010.000000          833.000000   -179.997929   
25%    15479.750000      2.000000          833.000000    -89.679759   
50%    30959.500000     14.000000          851.000000    -10.983115   
75%    46439.250000     84.000000          864.000000     81.964778   
max    61919.000000   6965.000000          864.000000    180.000000   

           latitude     longitude      speed_2d  
count  61920.000000  61920.000000  61477.000000  
mean      30.227762     -8.953367      2.558987  
std       14.809813      8.478471      3.576039  
min       12.354424    -17.626145      0.000000  
25%       15.393138    -16.761302      0.410000  
50%       30.424481     -9.662089      1.209049  
75%       49.999572      2.603591      3.059444  
max       51.518452      4.857561     63.488066

In [11]:
# convert in date_time data
df_raw["date_time"] = pd.to_datetime(df_raw["date_time"])

In [12]:
df_1 = df_raw[['date_time','bird_name', 'latitude', 'longitude','altitude']]
df_1['month'] = df_1.date_time.dt.month_name()

df_1

date_time bird_name   latitude  longitude  altitude  \
0     2013-08-15 00:18:08+00:00      Eric  49.419860   2.120733        71   
1     2013-08-15 00:48:07+00:00      Eric  49.419880   2.120746        68   
2     2013-08-15 01:17:58+00:00      Eric  49.420310   2.120885        68   
3     2013-08-15 01:47:51+00:00      Eric  49.420359   2.120859        73   
4     2013-08-15 02:17:42+00:00      Eric  49.420331   2.120887        69   
...                         ...       ...        ...        ...       ...   
61915 2014-04-30 22:00:08+00:00     Sanne  51.352572   3.177151        11   
61916 2014-04-30 22:29:57+00:00     Sanne  51.352585   3.177144         6   
61917 2014-04-30 22:59:52+00:00     Sanne  51.352622   3.177257         5   
61918 2014-04-30 23:29:43+00:00     Sanne  51.354641   3.181509        16   
61919 2014-04-30 23:59:34+00:00     Sanne  51.354474   3.181057         9   

        month  
0      August  
1      August  
2      August  
3      August  
4      August  
...       ...  
61915   April  
61916   April  
61917   April  
61918   April  
61919   April  

[61920 rows x 6 columns]

⁉## Calculate the distance covered per month¶


In [13]:
# create a line dataset
import geopandas as gpd
from shapely.geometry import Point, LineString

#zip the coordinates into a point object and convert to a GeoData Frame
geometry = [Point(xy) for xy in zip(df_1.longitude,df_1.latitude,)]
geo_df = gpd.GeoDataFrame(df_1, geometry=geometry)

In [14]:
geo_df.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 61920 entries, 0 to 61919
Data columns (total 7 columns):
 #   Column     Non-Null Count  Dtype              
---  ------     --------------  -----              
 0   date_time  61920 non-null  datetime64[ns, UTC]
 1   bird_name  61920 non-null  object             
 2   latitude   61920 non-null  float64            
 3   longitude  61920 non-null  float64            
 4   altitude   61920 non-null  int64              
 5   month      61920 non-null  object             
 6   geometry   61920 non-null  geometry           
dtypes: datetime64[ns, UTC](1), float64(2), geometry(1), int64(1), object(2)
memory usage: 3.3+ MB


In [15]:
geo_df = geo_df.groupby(['bird_name','month'])

In [16]:
geo_df

In [17]:
print(geo_df.describe())

                    latitude                                              \
                       count       mean        std        min        25%   
bird_name month                                                            
Eric      April       1557.0  49.497705   3.483398  37.220828  50.609380   
          August      1413.0  49.983468   0.212516  49.364336  49.938990   
          December    2585.0  30.436120   0.017376  30.339656  30.429446   
          February    2317.0  30.432094   0.015516  30.354953  30.429772   
          January     2574.0  30.414990   0.056114  30.174010  30.429607   
          March       2563.0  30.694484   1.185295  30.368229  30.429488   
          November    2081.0  40.020703   8.428037  30.362782  32.689036   
          October     2211.0  50.150249   0.076885  49.946324  50.087384   
          September   2494.0  50.156231   0.086908  49.848759  50.095452   
Nico      April       2228.0  27.276732  14.990132  12.425142  13.040279   
          Au

In [18]:
geo_df = geo_df['geometry']

In [19]:
geo_df.describe()

count unique  \
bird_name month                    
Eric      April      1557   1557   
          August     1413   1413   
          December   2585   2585   
          February   2317   2317   
          January    2574   2574   
          March      2563   2563   
          November   2081   2081   
          October    2211   2211   
          September  2494   2494   
Nico      April      2228   2228   
          August     1409   1409   
          December   2542   2542   
          February   2306   2306   
          January    2554   2554   
          March      2554   2554   
          November   2464   2464   
          October    2573   2573   
          September  2491   2491   
Sanne     April      2356   2356   
          August     1364   1364   
          December   2486   2486   
          February   2298   2298   
          January    2524   2524   
          March      2542   2542   
          November   2438   2438   
          October    2562   2562   
          September  2434   2434   

                                                                top freq  
bird_name month                                                           
Eric      April                       POINT (-6.9932118 37.2209056)    1  
          August                       POINT (2.1207332 49.4198595)    1  
          December                    POINT (-9.6432683 30.4288354)    1  
          February                    POINT (-9.6430307 30.4305882)    1  
          January             POINT (-9.6426517 30.430067600000005)    1  
          March                        POINT (-9.6430826 30.430299)    1  
          November             POINT (2.7320327 50.191300700000006)    1  
          October                       POINT (2.7324757 50.198221)    1  
          September   POINT (3.0292982000000004 50.365785200000005)    1  
Nico      April                      POINT (-16.7918027 12.6881279)    1  
          August               POINT (4.3945058 50.213454600000006)    1  
          December                   POINT (-15.4583946 24.2991759)    1  
          February   POINT (-16.475484299999998 15.986541399999998)    1  
          January            POINT (-16.354114199999998 18.9043874)    1  
          March              POINT (-17.1751286 14.532431699999998)    1  
          November             POINT (3.1136886 50.316199700000006)    1  
          October                      POINT (4.3941376 50.2133498)    1  
          September                    POINT (3.6088219 50.3694936)    1  
Sanne     April      POINT (-16.385496300000003 16.673008300000003)    1  
          August                       POINT (2.2818929 49.9310646)    1  
          December                   POINT (-16.7572634 14.0911268)    1  
          February           POINT (-17.0734882 14.257795800000002)    1  
          January                     POINT (-16.761063 14.0904587)    1  
          March              POINT (-16.642736300000003 15.9962489)    1  
          November                   POINT (-16.7702782 14.0907059)    1  
          October                    POINT (-16.7628055 14.0917737)    1  
          September                     POINT (-8.838542 41.890562)    1

In [20]:
geo_df= geo_df.apply(lambda x:LineString(x.tolist()))

In [21]:
geo_df = gpd.GeoDataFrame(geo_df, geometry='geometry',crs={'init':'epsg:4326'}).reset_index()
geo_df.to_crs(epsg=3310,inplace=True)
geo_df['distance (Km)'] = round(geo_df.length / 1000)

geo_df.head()

bird_name     month                                           geometry  \
0      Eric     April  LINESTRING (7805410.577 5205532.364, 7805418.4...   
1      Eric    August  LINESTRING (6774950.696 6344573.665, 6774948.8...   
2      Eric  December  LINESTRING (8406944.860 4690712.951, 8406943.2...   
3      Eric  February  LINESTRING (8406776.373 4690810.519, 8406721.6...   
4      Eric   January  LINESTRING (8406843.590 4690821.405, 8406836.6...   

   distance (Km)  
0         4559.0  
1          935.0  
2          606.0  
3          546.0  
4         1182.0

In [22]:
import altair as alt

source = geo_df

alt.Chart(source).mark_bar().encode(
    x=alt.X('bird_name:N',title=''),
    y='distance (Km):Q',
    color='bird_name:N',
    column=alt.Column('month:N',align="all",
                     sort=['August','September','October','November', 'December','January', 'February', 'March','April'])
)

alt.Chart(...)

## Show the routes through the time

In [23]:
df_Eric = df_raw[df_raw.bird_name=='Eric'].reset_index(drop=True)
df_Eric['date_time'] = df_Eric['date_time'].dt.date
df_Nico = df_raw[df_raw.bird_name=='Nico'].reset_index(drop=True)
df_Nico['date_time'] = df_Nico['date_time'].dt.date
df_Sanne = df_raw[df_raw.bird_name=='Sanne'].reset_index(drop=True)
df_Sanne['date_time'] = df_Sanne['date_time'].dt.date

In [24]:
import folium
from folium import plugins
from branca.element import Figure



# create the Heatmap
fig=Figure(width=850,height=550)

lat = df_raw.latitude.mean()
long = df_raw.longitude.mean()

m = folium.Map(location=[lat,long],zoom_start=3,tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',attr='Google_map')

fig.add_child(m)


lines = [
    {
        "coordinates": [[df_Eric.longitude[i],df_Eric.latitude[i]] for i in range(len(df_Eric))],
        "dates": df_Eric.date_time.astype(str).tolist(),
        "color": "red",
    },
    {
        "coordinates": [[df_Nico.longitude[i],df_Nico.latitude[i]] for i in range(len(df_Nico))],
        "dates": df_Nico.date_time.astype(str).tolist(),
        "color": "blue",
    },
    {
        "coordinates": [[df_Sanne.longitude[i],df_Sanne.latitude[i]] for i in range(len(df_Sanne))],
        "dates": df_Sanne.date_time.astype(str).tolist(),
        "color": "purple",
    }
]

features = [
    {
        "type": "Feature",
        "geometry": {
            "type": "LineString",
            "coordinates": line["coordinates"],
        },
        "properties": {
            "times": line["dates"],
            "style": {
                "color": line["color"],
                "weight": line["weight"] if "weight" in line else 2,
            },
            "popup": "Eric" if line["color"]== "red"  else "Nico" if line["color"]== "blue" else 'Sanne',
            "icon": "marker",
            "iconstyle": {
                "iconUrl":  "https://img.icons8.com/color/48/26e07f/seagull--v2.png" if line["color"]== "red"  else "https://img.icons8.com/fluency/48/000000/seagull.png",
                "iconSize": [50,50],
            }
        },
    }
    for line in lines
]

plugins.TimestampedGeoJson(
    {
        "type": "FeatureCollection",
        "features": features,
    },
    period="P1D",
    add_last_point=True,
    date_options='YYYY-MM-DD',
    loop_button=True,
    loop=False,).add_to(m)


plugins.Fullscreen().add_to(m)


m

## Find the pricese moment and the place where they met (if there are)

---



In [25]:
!pip install h3

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 6.9 MB/s eta 0:00:00


In [26]:
# create exagons
from h3 import h3

h3_level = 14 # ~6m2 area resolution

def lat_lng_to_h3(row):
    return h3.geo_to_h3(row.geometry.y, row.geometry.x, h3_level)

#zip the coordinates into a point object and convert to a GeoData Frame
geometry = [Point(xy) for xy in zip(df_1.longitude, df_raw.latitude)]
df_points = gpd.GeoDataFrame(df_1, geometry=geometry,crs="EPSG:4326")
df_points['h3'] = df_points.apply(lat_lng_to_h3, axis=1)
df_points['Date'] = df_points['date_time'].dt.to_period('D')
df_points.head()

date_time bird_name   latitude  longitude  altitude   month  \
0 2013-08-15 00:18:08+00:00      Eric  49.419860   2.120733        71  August   
1 2013-08-15 00:48:07+00:00      Eric  49.419880   2.120746        68  August   
2 2013-08-15 01:17:58+00:00      Eric  49.420310   2.120885        68  August   
3 2013-08-15 01:47:51+00:00      Eric  49.420359   2.120859        73  August   
4 2013-08-15 02:17:42+00:00      Eric  49.420331   2.120887        69  August   

                   geometry               h3        Date  
0  POINT (2.12073 49.41986)  8e1fb4b9065b8d7  2013-08-15  
1  POINT (2.12075 49.41988)  8e1fb4b9065b8c7  2013-08-15  
2  POINT (2.12088 49.42031)  8e1fb4b9065998f  2013-08-15  
3  POINT (2.12086 49.42036)  8e1fb4b90659917  2013-08-15  
4  POINT (2.12089 49.42033)  8e1fb4b90659837  2013-08-15

In [27]:
df_pol = df_points.groupby(['h3','Date','bird_name'],as_index=False).size()
df_pol = df_pol[df_pol.duplicated(subset=['h3','Date'],keep=False)]
df_pol

h3        Date bird_name  size
11024  8e194dc60c2a0cf  2014-04-25      Eric     1
11025  8e194dc60c2a0cf  2014-04-25      Nico     1
11288  8e194dc60d19d97  2014-04-25      Eric     1
11289  8e194dc60d19d97  2014-04-25     Sanne     1

In [28]:
# create a dataset with the geometry of the exagons and the number of earthquakes and max magnitudo
from shapely.geometry import Polygon

def add_geometry(row):
    points = h3.h3_to_geo_boundary(
      row['h3'], True)
    return Polygon(points)


df_pol['geometry'] = df_pol.apply(add_geometry, axis=1)
df_pol = gpd.GeoDataFrame(df_pol, crs='EPSG:4326')


df_pol

h3        Date bird_name  size  \
11024  8e194dc60c2a0cf  2014-04-25      Eric     1   
11025  8e194dc60c2a0cf  2014-04-25      Nico     1   
11288  8e194dc60d19d97  2014-04-25      Eric     1   
11289  8e194dc60d19d97  2014-04-25     Sanne     1   

                                                geometry  
11024  POLYGON ((3.17711 51.35012, 3.17709 51.35012, ...  
11025  POLYGON ((3.17711 51.35012, 3.17709 51.35012, ...  
11288  POLYGON ((3.17694 51.35228, 3.17692 51.35228, ...  
11289  POLYGON ((3.17694 51.35228, 3.17692 51.35228, ...

In [29]:
df_point = df_points.merge(df_pol[['h3','Date']],on=['h3','Date'],how='right') \
.drop_duplicates().reset_index(drop=True)

df_point['time'] = df_point['date_time'].dt.time

df_point

date_time bird_name   latitude  longitude  altitude  month  \
0 2014-04-25 21:13:38+00:00      Eric  51.350106   3.177105        20  April   
1 2014-04-25 20:09:48+00:00      Nico  51.350105   3.177092        -7  April   
2 2014-04-25 02:52:46+00:00      Eric  51.352257   3.176934        12  April   
3 2014-04-25 19:31:22+00:00     Sanne  51.352275   3.176927        22  April   

                   geometry               h3        Date      time  
0  POINT (3.17711 51.35011)  8e194dc60c2a0cf  2014-04-25  21:13:38  
1  POINT (3.17709 51.35011)  8e194dc60c2a0cf  2014-04-25  20:09:48  
2  POINT (3.17693 51.35226)  8e194dc60d19d97  2014-04-25  02:52:46  
3  POINT (3.17693 51.35227)  8e194dc60d19d97  2014-04-25  19:31:22

In [30]:
distance = df_point.to_crs({'init': 'epsg:6933'}).loc[0,'geometry'].distance(df_point.to_crs({'init': 'epsg:6340'}).loc[1,'geometry'])
distance_2 = df_point.to_crs({'init': 'epsg:6933'}).loc[2,'geometry'].distance(df_point.to_crs({'init': 'epsg:6340'}).loc[3,'geometry'])
print(f"""
      On 25th April 2014, Nico and Eric where at 20:09 and 21:13 respectively at {round(distance,2)} meters distance each other.
      It is highly probable that they met between 20:00 and 21:30.

      Eric and Sanne were nearby on the same day too ({round(distance_2,2)} meters), but the time gap is too wide that probably
      they did't cross each other.
      """)


      On 25th April 2014, Nico and Eric where at 20:09 and 21:13 respectively at 7842684.4 meters distance each other.
      It is highly probable that they met between 20:00 and 21:30.

      Eric and Sanne were nearby on the same day too (7842274.62 meters), but the time gap is too wide that probably
      they did't cross each other.
      


In [31]:
import folium
import branca
from folium import Figure
from folium.plugins import Fullscreen



df_base = df_point[['bird_name', 'geometry']].loc[:1]

# create a map
centroid = df_base.centroid
m = folium.Map(location=[centroid.y.mean(), centroid.x.mean()], zoom_start=15,tiles='OpenStreetMap')


# define map dimensions
fig=Figure(width=900,height=700)
fig.add_child(m)

style_function = lambda x: {'fillColor': '#0000ff' if
                             x['properties']['bird_name']=='Eric' else
                             '#00ff00'}

folium.GeoJson(data=df_base,
               style_function=style_function,
               tooltip=folium.GeoJsonTooltip(['bird_name'],labels=True,),
              ).add_to(m)



m

## Create a choropleth using the H3 geospatial indexing system to show where the birds spent more time

In [32]:
# create exagons
from h3 import h3

h3_level = 5 #~35Km2

def lat_lng_to_h3(row):
    return h3.geo_to_h3(row.geometry.y, row.geometry.x, h3_level)

#zip the coordinates into a point object and convert to a GeoData Frame
geometry = [Point(xy) for xy in zip(df_1.longitude, df_raw.latitude)]
geo_df = gpd.GeoDataFrame(df_1, geometry=geometry,crs="EPSG:4326")
geo_df['h3'] = geo_df.apply(lat_lng_to_h3, axis=1)
geo_df['Date'] = geo_df['date_time'].dt.to_period('D')
geo_df.head()

df_hexagon = geo_df.groupby(['bird_name','h3']).agg(number_of_points = ('h3','count')).reset_index()

df_hexagon.head()

bird_name               h3  number_of_points
0      Eric  85184123fffffff                 1
1      Eric  8518412ffffffff                 1
2      Eric  85184187fffffff                 1
3      Eric  851841abfffffff                 1
4      Eric  851841bbfffffff                 1

In [33]:
# create a dataset with the geometry of the exagons and the number of earthquakes and max magnitudo
from shapely.geometry import Polygon

def add_geometry(row):
    points = h3.h3_to_geo_boundary(
      row['h3'], True)
    return Polygon(points)


df_hexagon['geometry'] = df_hexagon.apply(add_geometry, axis=1)
df_hexagon = gpd.GeoDataFrame(df_hexagon, crs="EPSG:4326")

df_hexagon.head()

bird_name               h3  number_of_points  \
0      Eric  85184123fffffff                 1   
1      Eric  8518412ffffffff                 1   
2      Eric  85184187fffffff                 1   
3      Eric  851841abfffffff                 1   
4      Eric  851841bbfffffff                 1   

                                            geometry  
0  POLYGON ((-2.38032 45.76828, -2.47364 45.71323...  
1  POLYGON ((-2.45072 45.62408, -2.54384 45.56886...  
2  POLYGON ((-2.09604 46.34259, -2.19019 46.28825...  
3  POLYGON ((-2.23872 46.05593, -2.33245 46.00124...  
4  POLYGON ((-2.16751 46.19938, -2.26146 46.14487...

In [34]:
import folium
import branca
from folium import Figure
from folium.plugins import Fullscreen


df_base = df_hexagon


# create a map
centroid = df_base.centroid
m = folium.Map(location=[centroid.y.mean(), centroid.x.mean()], zoom_start=4,control_scale=False,tiles=None )

tile_layer = folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',
    attr='Google_map',
    control=False,
    opacity=1
)
tile_layer.add_to(m)

# define map dimensions
fig=Figure(width=900,height=700)
fig.add_child(m)

for var in df_base['bird_name'].unique():
    df_geo = df_base[df_base['bird_name']==var]

    c = folium.Choropleth(
        geo_data=df_geo.to_json(),
        name=var,
        data=df_geo,
        columns=["h3", 'number_of_points'],
        key_on="feature.properties.h3",
        fill_color='Reds',
        fill_opacity=0.6,
        legend_name=var,
        overlay=False,
        highlight=True,
        line_opacity=.8,
    ).add_child(folium.TileLayer(tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',attr='Google_map')).add_to(m)


    for key in list(c._children):
        if key.startswith('color_map'):
            del(c._children[key])

    c.geojson.add_child(folium.features.GeoJsonTooltip(fields=['number_of_points'],
                                                       aliases=['number_of_points'],
                                                       style=('background-color: white; color: black; font-family:''Courier New; font-size: 12px; padding: 10px;')
                                                      )
                       )



# Add a layer control panel to the map.
m.add_child(folium.LayerControl(collapsed=True))

#fullscreen
folium.plugins.Fullscreen().add_to(m)


m